In [13]:
import pandas as pd
import matplotlib.pyplot as plt
from pandas.api.types import is_numeric_dtype
stack_dfs = pd.read_csv("StateGovFinances2005to2021.csv", index_col = ["State", "Year", "Format"], low_memory =False).sort_index()
panel_dfs_dict = {k:stack_dfs[stack_dfs.index.get_level_values(2)==k].reset_index().set_index(["State","Year"]).sort_index() for k in stack_dfs.index.get_level_values(2).unique()}
for key, df in panel_dfs_dict.items():
    for col in df.columns:
        if not is_numeric_dtype(df[col]):
            try:
                df[col] = pd.to_numeric(df[col], errors = "coerce")
                df[col] = df[col].fillna(0)
                df[col] = df[col].astype(int)
            except:
                pass
        else:
            df[col] = df[col].fillna("")



In [14]:
efwgdp = pd.read_csv("EFWGDPTaxes.csv", parse_dates = ["Year"]).set_index(["State", "Year"]).sort_index()
efwgdp[["EFW", "GDP"]]

EFW           GDP
State Year                          
AK    1985-01-01  8.04           NaN
      1986-01-01   NaN           NaN
      1987-01-01   NaN           NaN
      1988-01-01   NaN           NaN
      1989-01-01   NaN           NaN
...                ...           ...
WY    2019-01-01  8.12  3.997140e+10
      2020-01-01  7.97  3.667550e+10
      2021-01-01   NaN  4.217620e+10
      2022-01-01   NaN  4.908060e+10
      2023-01-01   NaN  5.017160e+10

[1950 rows x 2 columns]

In [22]:
plot_dfs = {}
keys = ["GENERAL REVENUE","GENERAL REVENUE FROM OWN SOURCES", "EXPENDITURE", "FROM FEDERAL GOVERNMENT", "FROM LOCAL GOVERNMENTS" ,"TAXES", "OTHER TAXES", "CURRENT CHARGES", "OTHER CHARGES", 'INDIVIDUAL INCOME', 'CORPORATE INCOME', 
        "PROPERTY", "SPECIAL ASSESSMENTS",
        "SALES AND GROSS RECEIPTS", "GENERAL SALES", "MOTOR FUEL", "GAS SUPPLY", "EDUCATION", "HIGHER EDUCATION", "PUBLIC WELFARE"]	
keys = ["1" + k for k in keys]
plot_dfs["Level"] = panel_dfs_dict['State & local government amount'][keys]
plot_dfs["Level"].rename(columns = {k:k.replace("1", "").title() for k in plot_dfs["Level"].keys()}, inplace = True)
plot_dfs["Level"]["Total Income"] = plot_dfs["Level"]["Individual Income"].add(plot_dfs["Level"]["Corporate Income"])
plot_dfs["Level"]["Deficit"] = plot_dfs["Level"]["Expenditure"].sub(plot_dfs["Level"]["General Revenue"])
plot_dfs["Level"]["GDP"] = efwgdp["GDP"]
plot_dfs["Level"]["Population"] = efwgdp["Population"]

plot_dfs["Percent of General Revenue"] = plot_dfs["Level"].apply(lambda x: x.div(plot_dfs["Level"]["General Revenue"]) if is_numeric_dtype(x) else x)    
plot_dfs["Percent of GDP"] = plot_dfs["Level"].apply(lambda x: x.div(plot_dfs["Level"]["GDP"]) if is_numeric_dtype(x) else x)

plot_dfs["Value of Per Capita"] = plot_dfs["Level"].apply(lambda x: x.div(plot_dfs["Level"]["Population"]) if is_numeric_dtype(x) else x)    

for key in plot_dfs.keys():
    plot_dfs[key]["EFW"] = efwgdp["EFW"]

/tmp/ipykernel_16626/2813009934.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_16626/2813009934.py:8: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_16626/2813009934.py:9: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_16626/2813009934.py:10: SettingWithCopyWarning:


A value 

In [23]:
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from plotly.subplots import make_subplots
from homebrewedFunctions.functions import *

In [41]:
from homebrewedFunctions.functions import *
def line_dropdown(df):
    plot_df = df.reset_index()
    fig = px.line(plot_df, x="Year", y="General Revenue", color="State")
                        #   text = df.index.get_level_values(0) + ": " + df.index.get_level_values(1))
    initial_hovertemplate = f"%{{x}}<br>%{{yaxis.title.text}}: %{{y}}"
    fig.update_traces(hovertemplate=initial_hovertemplate)

    y_buttons = []
    for col in df.columns:
        if is_numeric_dtype(df[col]):
            y_buttons.append(
                dict(
                    args=[
                        {"y": [df.loc[state][col] for state in plot_df['State'].unique()]},
                        {"yaxis.title.text": col}
                    ],
                    label=col,
                    method="update"
                )
            )

    fig.update_layout(
        updatemenus=[
            dict(
                buttons=y_buttons,
                direction="down",
                showactive=True,
                x=0.17,
                xanchor="left",
                y=1.15,
                yanchor="top"
            ),
            dict(
                type="buttons",
                direction="left",
                buttons=list([
                    dict(
                        args=[{"yaxis.type": "linear"}],
                        label="Linear Y",
                        method="relayout"
                    ),
                    dict(
                        args=[{"yaxis.type": "log"}],
                        label="Log Y",
                        method="relayout"
                )
            ]))
        ],
    )

    return fig

figs = {key: line_dropdown(dataframe) for key, dataframe in plot_dfs.items()}
fig = dict_of_figs_to_dropdown_fig(figs, show_fig = False,
                                 use_sliders = True)
fig.show()
fig.write_html(f"outputs/StateFinancesAsPercentRevenuePercentGDPAndPerCapitaFigs.html")

# fig = line_dropdown(pct_df)
# fig.write_html("line_dropdown.html")

In [32]:
figs["Level"].__dict__

{'_validate': True,
 '_grid_str': 'This is the format of your plot grid:\n[ (1,1) x,y ]\n',
 '_grid_ref': [[(SubplotRef(subplot_type='xy', layout_keys=('xaxis', 'yaxis'), trace_kwargs={'xaxis': 'x', 'yaxis': 'y'}),)]],
 '_data_validator': <plotly.validators._data.DataValidator at 0x7230a83e0d10>,
 '_data_objs': [Scatter({
      'hovertemplate': '%{name}: %{x}<br>%{yaxis.title.text}: %{y}',
      'legendgroup': 'AK',
      'line': {'color': '#636efa', 'dash': 'solid'},
      'marker': {'symbol': 'circle'},
      'mode': 'lines',
      'name': 'AK',
      'orientation': 'v',
      'showlegend': True,
      'x': array(['2005-01-01', '2006-01-01', '2007-01-01', '2008-01-01', '2009-01-01',
                  '2010-01-01', '2011-01-01', '2012-01-01', '2013-01-01', '2014-01-01',
                  '2015-01-01', '2016-01-01', '2017-01-01', '2018-01-01', '2019-01-01',
                  '2020-01-01', '2021-01-01'], dtype=object),
      'xaxis': 'x',
      'y': array([ 9824780., 11023466., 12967609

In [25]:
for key in 
create_scatter_dropdown(pct_df, 
                        filename = "IncomePropertyAssessmentSalesFuelTaxesPctTotalRevenue.html", 
                        show_fig = True)



NameError: name 'pct_df' is not defined

In [ ]:
pct_df.values